**Table of contents**<a id='toc0_'></a>    
- [State Farm](#toc1_)    
  - [Intro](#toc1_1_)    
    - [Train](#toc1_1_1_)    
    - [Test](#toc1_1_2_)    
    - [Introductory Conclusions](#toc1_1_3_)    
  - [EDA](#toc1_2_)    
    - [Train](#toc1_2_1_)    
    - [Test](#toc1_2_2_)    
    - [EDA Conclusions](#toc1_2_3_)    
  - [Preprocessing](#toc1_3_)    
      - [Preprocessing Conclusions](#toc1_3_1_1_)    
  - [Modeling](#toc1_4_)    
    - [Tuning with Grid Search CV](#toc1_4_1_)    
    - [Tuning Neural Network](#toc1_4_2_)    
      - [Model Pipeline](#toc1_4_2_1_)    
    - [Compare Model Scores](#toc1_4_3_)    
      - [Dummy Model AUC](#toc1_4_3_1_)    
      - [Logistic Regression AUC](#toc1_4_3_2_)    
      - [Decision Tree AUC](#toc1_4_3_3_)    
      - [Random Forest AUC](#toc1_4_3_4_)    
      - [SVM AUC](#toc1_4_3_5_)    
      - [XG Boost AUC](#toc1_4_3_6_)    
      - [Light GBM AUC](#toc1_4_3_7_)    
        - [Modelling Conclusions](#toc1_4_3_7_1_)    
    - [Feature Importance](#toc1_4_4_)    
      - [Logistic Regression](#toc1_4_4_1_)    
      - [Decision Tree](#toc1_4_4_2_)    
      - [Random Forest](#toc1_4_4_3_)    
      - [Support Vector](#toc1_4_4_4_)    
      - [XG Boost](#toc1_4_4_5_)    
      - [Light GBM](#toc1_4_4_6_)    
  - [Simulate Scoring with Test Set](#toc1_5_)    
      - [Test Set scoring Predictions](#toc1_5_1_1_)    
  - [Final Model Predictions](#toc1_6_)    
  - [Executive Summary](#toc1_7_)    

<!-- vscode-jupyter-toc-config
	numbering=false
	anchor=true
	flat=false
	minLevel=1
	maxLevel=6
	/vscode-jupyter-toc-config -->
<!-- THIS CELL WILL BE REPLACED ON TOC UPDATE. DO NOT WRITE YOUR TEXT IN THIS CELL -->

# <a id='toc1_'></a>[State Farm](#toc0_)

## <a id='toc1_1_'></a>[Intro](#toc0_)

In [1]:
# import libraries
import pandas as pd 
import plotly_express as px 
import plotly.graph_objects as go  
import numpy as np    
from sklearn.model_selection import train_test_split, cross_val_score, GridSearchCV
from sklearn.dummy import DummyClassifier
from sklearn.linear_model import LogisticRegression
from sklearn.ensemble import RandomForestClassifier, VotingClassifier
from sklearn.tree import DecisionTreeClassifier
from sklearn import svm
from xgboost import XGBClassifier
from lightgbm import LGBMClassifier
from sklearn.pipeline import Pipeline
from sklearn.preprocessing import StandardScaler, OrdinalEncoder, LabelEncoder
from sklearn.neural_network import MLPClassifier
from tensorflow import keras
from tensorflow.keras.optimizers import Adam
from sklearn.experimental import enable_iterative_imputer
from sklearn.impute import SimpleImputer, KNNImputer, IterativeImputer
from sklearn.metrics import accuracy_score, auc, roc_auc_score, roc_curve, f1_score, classification_report, confusion_matrix


In [2]:
# read dataset 
train = pd.read_csv('datasets/exercise_40_train.csv')
test = pd.read_csv('datasets/exercise_40_test.csv')

In [3]:
# set max column length to 105
pd.set_option('display.max_columns', 110)

### <a id='toc1_1_1_'></a>[Train](#toc0_)

In [4]:
# look at dataset
train.head()

y        x1         x2        x3        x4        x5        x6        x7  \
0  0  0.165254  18.060003       Wed  1.077380 -1.339233 -1.584341   0.0062%   
1  1  2.441471  18.416307    Friday  1.482586  0.920817 -0.759931   0.0064%   
2  1  4.427278  19.188092  Thursday  0.145652  0.366093  0.709962   -8e-04%   
3  0  3.925235  19.901257   Tuesday  1.763602 -0.251926 -0.827461  -0.0057%   
4  0  2.868802  22.202473    Sunday  3.405119  0.083162  1.381504   0.0109%   

         x8        x9       x10         x11       x12       x13       x14  \
0  0.220784  1.816481  1.171788  109.626841  4.644568  4.814885  1.541740   
1  1.192441  3.513950  1.419900   84.079367  1.459868  1.443983       NaN   
2  0.952323  0.782974 -1.247022   95.375221  1.098525  1.216059  0.450624   
3 -0.520756  1.825586  2.223038   96.420382 -1.390239  3.962961       NaN   
4 -0.732739  2.151990 -0.275406   90.769952  7.230125  3.877312  0.392002   

        x15         x16       x17        x18                 x19       x20  \
0 -0.587361  101.906052  4.278444  77.709700  $-908.650758424405  7.328029   
1 -1.165869  100.112121  8.487132  70.808566   $-1864.9622875143  6.796408   
2  0.211685   99.215210  8.601193  75.922820  $-543.187402955527  3.802395   
3 -2.046856         NaN  6.611554  74.966925  $-182.626380634258  7.728963   
4 -1.201565  100.626558  9.103015  77.977156   $967.007090837503  2.272765   

         x21         x22       x23     x24       x25       x26          x27  \
0  36.601967  126.384294  1.264713  female  3.834082  2.352406   905.491445   
1   3.789176   93.037021  0.346201    male  4.345028  1.651579   868.784447   
2   7.407996   71.022413  0.070968    male  4.332644 -0.375737  1077.233497   
3   8.136213  121.610846  0.700954    male  7.294990 -0.603983  1051.655489   
4  24.452102   56.492317 -1.102387    male  6.313827  0.429187   949.904947   

         x28       x29  x30  x31       x32        x33        x34       x35  \
0  14.779467  0.752524  NaN   no -0.597288   Colorado  46.667221  3.159002   
1  25.914680  1.445294  NaN   no  1.127376  Tennessee  47.928569 -1.013712   
2  13.177479  4.174536  NaN   no  2.605279      Texas  56.674425  0.108486   
3  17.006528  2.347355  NaN   no  1.071202  Minnesota  59.154933  1.319711   
4  16.962710  0.510985  NaN  yes  2.283921   New York  46.445617  0.022747   

         x36        x37        x38         x39        x40            x41  \
0  69.444841  32.450076        NaN  5-10 miles  18.129499            NaN   
1  61.289132  35.521824  31.526217  5-10 miles  11.389081   99074.100620   
2  69.798923  30.684074  31.049447  5-10 miles  14.372443  100087.339539   
3  65.408246  34.401290  48.363690  5-10 miles  13.191173  100934.096543   
4  66.662910  31.135261  31.819899  5-10 miles  17.210430            NaN   

        x42       x43       x44       x45       x46        x47        x48  \
0  0.904626  1.227266  0.703326 -0.810371  0.234654  53.359113  58.251700   
1 -1.157897 -0.822055 -0.851141  2.651773  1.104631  37.728834  56.052749   
2  0.869508  0.150728       NaN -0.856591 -2.561083  50.236892  63.975108   
3       NaN -0.965711       NaN  0.422522 -2.123048  41.857197  59.226119   
4       NaN  1.012093       NaN -0.348240  3.477451  47.844153  55.921988   

         x49          x50       x51        x52        x53       x54       x55  \
0  16.084987  1602.756464  2.740134   7.617666  72.167186  0.166127       NaN   
1        NaN  3350.837875  1.995635        NaN  73.964560       NaN       NaN   
2   6.998154  3756.910196  1.772648  15.057485  59.428690  1.844493       NaN   
3        NaN  1961.609788  3.155214        NaN  68.671023 -1.020225  5.833712   
4        NaN  2345.195505  3.253079  14.193721  71.853326  0.926779  4.115990   

        x56  x57         x58  x59        x60       x61       x62       x63  \
0 -1.532562  NaN  300.629990    0     August  9.840873  6.600008  1.252479   
1  0.956001  NaN  300.629990    0      April  6.939395  3.864254  0.057936   
2  4.127857

At first glance, we see various problems with the dataset, and we collect some ideas of how to deal with those problems: label encode x3, remove % in x7, fill missing values, remove dollar sign in x19, binarize x24, binarize x31, label encode x33, label encode x39, label encode x60, label encode x64, label encode x65, label encode x77, binarize x93, binarize x99. THe most efficient method would be to use a pipeline to label encode and impute missing values. 

In [5]:
# summary info on columns
train.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 40000 entries, 0 to 39999
Columns: 101 entries, y to x100
dtypes: float64(86), int64(3), object(12)
memory usage: 30.8+ MB


In [6]:
# looking at shape of data
train.shape

(40000, 101)

In [7]:
# looking at column names
train.columns

Index(['y', 'x1', 'x2', 'x3', 'x4', 'x5', 'x6', 'x7', 'x8', 'x9',
       ...
       'x91', 'x92', 'x93', 'x94', 'x95', 'x96', 'x97', 'x98', 'x99', 'x100'],
      dtype='object', length=101)

In [8]:
# remove special characters
train.x7 = train.x7.str.replace('%', '').astype(float)
train.x19 = train.x19.str.replace('$', '').astype(float)

C:\Users\XIX\AppData\Local\Temp\ipykernel_23216\2428904411.py:3: FutureWarning: The default value of regex will change from True to False in a future version. In addition, single character regular expressions will *not* be treated as literal strings when regex=True.
  train.x19 = train.x19.str.replace('$', '').astype(float)


In [9]:
# Check proper implementation
train[['x7', 'x19']].head()

x7          x19
0  0.0062  -908.650758
1  0.0064 -1864.962288
2 -0.0008  -543.187403
3 -0.0057  -182.626381
4  0.0109   967.007091

We needed to remove the special characters from the dataset, and then convert those columns into float. By default, x19 was rounded to 6 decimal places. This should have a minimal effect on the model performance. 

In [10]:
# looking at categories
train.select_dtypes(['object'])

x3     x24  x31        x33         x39        x60          x65  \
0           Wed  female   no   Colorado  5-10 miles     August      farmers   
1        Friday    male   no  Tennessee  5-10 miles      April     allstate   
2      Thursday    male   no      Texas  5-10 miles  September        geico   
3       Tuesday    male   no  Minnesota  5-10 miles  September        geico   
4        Sunday    male  yes   New York  5-10 miles    January        geico   
...         ...     ...  ...        ...         ...        ...          ...   
39995       Sun  female   no        NaN  5-10 miles       July      farmers   
39996  Thursday    male  yes   Illinois  5-10 miles       July  progressive   
39997    Monday    male  yes        NaN  5-10 miles     August        geico   
39998   Tuesday    male   no       Ohio  5-10 miles   December      farmers   
39999  Thursday     NaN   no    Florida  5-10 miles    January  progressive   

            x77  x93  x99  
0      mercedes   no  yes  
1      mercedes   no  yes  
2        subaru   no  yes  
3        nissan   no  yes  
4        toyota  yes  yes  
...         ...  ...  ...  
39995       NaN   no  yes  
39996      ford   no  yes  
39997      ford   no  yes  
39998       NaN   no  yes  
39999    toyota   no  NaN  

[40000 rows x 10 columns]

We need to take a better look at the object columns with EDA. 

In [11]:
# rows with missing values
train.isna().any(axis=1).sum()

39999

We see that most rows have at least one missing value

In [12]:
# checking for rows where all values are missing 
train.isna().all(axis=0).sum()

0

Dataset does not contain any rows where all values are missing.

In [13]:
# looking for duplicates
train.duplicated().sum()

0

### <a id='toc1_1_2_'></a>[Test](#toc0_)

In [14]:
# look at test set
test.head()

x1         x2         x3        x4        x5        x6       x7  \
0  4.747627  20.509439  Wednesday  2.299105 -1.815777 -0.752166  0.0098%   
1  1.148654  19.301465        Fri  1.862200 -0.773707 -1.461276  0.0076%   
2  4.986860  18.769675   Saturday  1.040845 -1.548690  2.632948  -5e-04%   
3  3.709183  18.374375    Tuesday -0.169882 -2.396549 -0.784673  -0.016%   
4  3.801616  20.205541     Monday  2.092652 -0.732784 -0.703101  0.0186%   

         x8        x9       x10         x11       x12       x13       x14  \
0 -3.240309  0.587948 -0.260721  101.113628 -0.812035  3.251085 -0.004432   
1  0.443209  0.522113 -1.090886  104.791999  8.805876  1.651993       NaN   
2 -1.167885  5.739275  0.222975  102.109546  7.831517  3.055358  2.036434   
3 -2.662226  1.548050  0.210141   82.653354  0.436885  1.578106       NaN   
4  0.056422  2.878167 -0.457618   75.036421  8.034303  1.631426  0.643738   

        x15         x16        x17        x18                 x19       x20  \
0 -0.917763  102.193597   7.097387  75.256714   $120.216189955777  8.269754   
1 -1.396065   99.356609   7.117930  79.061540  $-267.562586413086  5.668347   
2  1.057296         NaN  10.943217  87.567827  $-311.292903116571  3.219583   
3 -1.287913  102.410965   6.588790  71.825782   $2229.14940030076  7.459929   
4  0.349166  101.513490   5.777599  74.602441  $-469.049529991235  8.245194   

         x21        x22       x23     x24       x25       x26          x27  \
0   4.794438  56.134458 -0.083641     NaN  5.740955 -3.152540   924.013304   
1  12.377178        NaN  0.321981  female  2.058123 -0.442525  1107.628399   
2  31.135956  50.048638  1.174485    male  1.609278 -0.303259  1009.911508   
3   1.822459  88.144007  0.909556  female  8.864059  0.641209   841.889126   
4   0.904920  51.705319 -0.544762  female  2.408958  1.841905   885.172420   

         x28       x29  x30  x31       x32             x33        x34  \
0  17.697125  1.402273  NaN   no  1.461654         Florida  57.930285   
1  15.747234  2.027073  NaN  yes  0.608259  North Carolina  55.646392   
2  12.008190  0.618778  NaN   no  0.680923             NaN  53.178113   
3  20.904196  0.725017  NaN   no  0.622849     Mississippi  50.311869   
4  14.401750  4.059599  NaN  yes  1.073262         Georgia  39.646787   

        x35        x36        x37        x38         x39        x40  \
0  4.727300  66.416594  28.450466  33.499310  5-10 miles  16.776061   
1  0.789132  68.881807  32.242558  -1.034680  5-10 miles  11.959804   
2  0.869321  70.249633  35.207243  48.980294  5-10 miles  14.564732   
3  0.453211  65.253390  34.432292  52.756665  5-10 miles  18.503815   
4 -0.686812  71.673393  37.257458  64.572325  5-10 miles  11.477353   

             x41       x42       x43       x44       x45       x46        x47  \
0   99971.844703  0.492812 -0.963616       NaN       NaN  1.266416  53.020326   
1   99910.554923  0.547935  1.001799  1.315020  3.229084  5.873890  49.116516   
2  100729.380783  0.096947 -0.490053       NaN  1.333292  0.750075  48.258898   
3  101476.778846  0.888038 -0.007376 -1.126059  1.129508 -0.455920  44.525657   
4   99444.069807  0.597749  0.432984       NaN  2.973636  2.684343  46.377723   

         x48        x49          x50       x51       x52        x53       x54  \
0  61.840284        NaN  1825.413159  2.517924       NaN  70.880778       NaN   
1  61.279131   9.360134  1818.390072  2.269700  0.336755  69.832156  2.666487   
2  63.737244  11.564194  1815.680559  1.704048       NaN  67.090400  1.547230   
3  60.008453  12.852088  2251.680231  2.915405  5.895661  75.219207       NaN   
4  55.276157  15.245726  3377.213091  0.461064  9.296694  64.547880  2.196671   

        x55       x56  x57        x58  x59      x60        x61       x62  \
0  1.923125  0.239009  NaN  300.62999    0      May   5.461123  5.149473   
1  1.224195 -1.214940  NaN  300.62999    0     July   6.520113  2.101449   
2       NaN  1.428580  NaN  300.62999    0  January  12.190433  1.793349   
3

In [15]:
# shape of dataset
test.shape

(10000, 100)

In [16]:
# look at info on columns
test.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 10000 entries, 0 to 9999
Data columns (total 100 columns):
 #   Column  Non-Null Count  Dtype  
---  ------  --------------  -----  
 0   x1      10000 non-null  float64
 1   x2      10000 non-null  float64
 2   x3      10000 non-null  object 
 3   x4      10000 non-null  float64
 4   x5      9398 non-null   float64
 5   x6      10000 non-null  float64
 6   x7      10000 non-null  object 
 7   x8      10000 non-null  float64
 8   x9      10000 non-null  float64
 9   x10     10000 non-null  float64
 10  x11     8671 non-null   float64
 11  x12     10000 non-null  float64
 12  x13     10000 non-null  float64
 13  x14     7572 non-null   float64
 14  x15     10000 non-null  float64
 15  x16     7247 non-null   float64
 16  x17     10000 non-null  float64
 17  x18     10000 non-null  float64
 18  x19     10000 non-null  object 
 19  x20     10000 non-null  float64
 20  x21     10000 non-null  float64
 21  x22     9387 non-null   float64
 22

In [17]:
# looking at missing values
test.isna().sum()

x1         0
x2         0
x3         0
x4         0
x5       602
        ... 
x96     1628
x97        0
x98        0
x99     3300
x100       0
Length: 100, dtype: int64

In [18]:
# remove special characters
test.x7 = test.x7.str.replace('%', '').astype(float)
test.x19 = test.x19.str.replace('$', '').astype(float)

C:\Users\XIX\AppData\Local\Temp\ipykernel_23216\4155689457.py:3: FutureWarning: The default value of regex will change from True to False in a future version. In addition, single character regular expressions will *not* be treated as literal strings when regex=True.
  test.x19 = test.x19.str.replace('$', '').astype(float)


In [19]:
# Check proper implementation
test[['x7', 'x19']].head()

x7          x19
0  0.0098   120.216190
1  0.0076  -267.562586
2 -0.0005  -311.292903
3 -0.0160  2229.149400
4  0.0186  -469.049530

### <a id='toc1_1_3_'></a>[Introductory Conclusions](#toc0_)

We cleaned the data from the obvious issues, such as special characters and changing dtypes. We see manny missing values as well as categorical columns in the dataset. We applied the same cleaning methods to both the training and test sets. 

## <a id='toc1_2_'></a>[EDA](#toc0_)

### <a id='toc1_2_1_'></a>[Train](#toc0_)

In [20]:
# values of column
train.x3.value_counts(dropna=False)

Wednesday    4930
Monday       4144
Friday       3975
Tuesday      3915
Sunday       3610
Saturday     3596
Tue          2948
Thursday     2791
Mon          2200
Wed          2043
Sat          1787
Thur         1643
Fri          1620
Sun           798
Name: x3, dtype: int64

In [21]:
# being consistent with labeling, short notation
train.x3 = train.x3.str.replace('Sunday', 'Sun')
train.x3 = train.x3.str.replace('Monday', 'Mon')
train.x3 = train.x3.str.replace('Tuesday', 'Tue')
train.x3 = train.x3.str.replace('Wednesday', 'Wed')
train.x3 = train.x3.str.replace('Thursday', 'Thur')
train.x3 = train.x3.str.replace('Friday', 'Fri')
train.x3 = train.x3.str.replace('Saturday', 'Sat')

We combined the corresponding days to the shorthand notation. 

In [22]:
# values of column
train.x24.value_counts(dropna=False)

female    18158
male      17986
NaN        3856
Name: x24, dtype: int64

In [23]:
# check values
train.x33.value_counts(dropna=False)

NaN               7171
California        3393
Texas             2252
Florida           1802
New York          1714
Illinois          1240
Pennsylvania      1233
Ohio              1114
Michigan           982
Georgia            918
North Carolina     910
New Jersey         870
Virginia           791
Washington         750
Tennessee          690
Indiana            674
Arizona            665
Massachusetts      638
Wisconsin          635
Missouri           634
Minnesota          611
Maryland           581
Alabama            554
Colorado           530
Louisiana          501
South Carolina     491
Kentucky           478
Oregon             452
Connecticut        422
Oklahoma           397
Kansas             378
Nevada             373
Utah               370
Mississippi        361
Iowa               353
Arkansas           346
New Mexico         333
Nebraska           323
West Virginia      305
Hawaii             282
Idaho              277
Maine              247
Rhode Island       246
New Hampshi

There are 52 values for what is a states column. Total should be 50 + 1 with D.C. Therefore, the missing value is not a missing state or territory from the list. The values will be imputed in the pipeline. 

In [24]:
# Change values to 1
train.x39 = train.x39.str.replace('5-10 miles', '1').astype(int)

All rows of this column are the same, so we will change the value to 1. 

In [25]:
# checking values
train.x60.value_counts(dropna=False)

December     8136
January      7922
July         7912
August       7907
June         1272
September    1245
February     1213
November     1043
April         951
March         807
May           799
October       793
Name: x60, dtype: int64

This column represents months. No duplicate naming is seen here, and all 12 months are present. 

In [26]:
# checking values
train.x65.value_counts(dropna=False)

progressive    10877
allstate       10859
esurance        7144
farmers         5600
geico           5520
Name: x65, dtype: int64

This column represents the different insurance companies. 

In [27]:
# checking values
train.x77.value_counts(dropna=False)

NaN          9257
ford         9005
subaru       5047
chevrolet    5011
mercedes     4494
toyota       3555
nissan       2575
buick        1056
Name: x77, dtype: int64

This column represents different vehicle manufacturers. As it is unlikely that the missing values are all one manufacturer missing from the list, these values will have to be imputed. 

In [28]:
# checking values
train.x93.value_counts(dropna=False)

no     35506
yes     4494
Name: x93, dtype: int64

In [29]:
# values of column
train.x99.value_counts(dropna=False)

yes    27164
NaN    12836
Name: x99, dtype: int64

Missing values in this column are more likely to be no, rather than missing yes values. Therefore, we will fill in missing vales with no. 

In [30]:
# fill missing values with no
train.x99.fillna('no', inplace=True)

In [31]:
# check proper implementation
train.x99.value_counts(dropna=False)

yes    27164
no     12836
Name: x99, dtype: int64

Filled missing values with no.

In [32]:
# summary statistics on data
train.describe()

y            x1            x2            x4            x5  \
count  40000.000000  40000.000000  40000.000000  40000.000000  37572.000000   
mean       0.145075      2.999958     20.004865      0.002950      0.005396   
std        0.352181      1.994490      1.604291      1.462185      1.297952   
min        0.000000     -3.648431     13.714945     -5.137161     -5.616412   
25%        0.000000      1.592714     18.921388     -1.026798     -0.872354   
50%        0.000000      2.875892     20.005944      0.002263      0.008822   
75%        0.000000      4.270295     21.083465      1.043354      0.892467   
max        1.000000     13.837591     27.086468      5.150153      5.698128   

                 x6            x7            x8            x9           x10  \
count  40000.000000  40000.000000  40000.000000  40000.000000  40000.000000   
mean       0.007234      0.000033      0.004371      2.722334      0.490339   
std        1.358551      0.009965      1.447223      1.966828      1.029863   
min       -6.113153     -0.043800     -6.376810     -3.143438     -3.538129   
25%       -0.909831     -0.006700     -0.971167      1.340450     -0.207833   
50%        0.007335      0.000100      0.002226      2.498876      0.486926   
75%        0.926222      0.006800      0.985023      3.827712      1.182994   
max        5.639372      0.037900      5.869889     18.006669      4.724186   

                x11           x12           x13           x14           x15  \
count  34890.000000  40000.000000  40000.000000  30136.000000  40000.000000   
mean     100.008988      3.039317      3.881807      0.787999      0.011162   
std       13.343010      3.575534      2.678838      0.751117      1.480175   
min       50.526543     -5.846331     -3.060994     -0.338985     -6.141315   
25%       91.056682     -0.200773      1.987650      0.189364     -0.986405   
50%      100.020965      3.073967      3.444608      0.677067      0.016980   
75%      109.025025      6.266835      5.319072      1.267256      1.007430   
max      148.784484     11.149273     25.634165      4.291924      5.930678   

                x16           x17           x18           x19           x20  \
count  28788.000000  40000.000000  40000.000000  40000.000000  40000.000000   
mean     100.702408      8.005758     79.936742     -5.028013      4.962774   
std        1.058560      2.270345      6.514228   1001.312630      3.544050   
min       99.131018     -1.384508     66.756855  -4166.106634     -9.561032   
25%       99.857805      6.465327     74.015148   -682.694719      2.558445   
50%      100.540700      8.003181     79.857023      0.692233      4.982334   
75%      101.371152      9.537869     85.907545    670.404666      7.337529   
max      104.753426     18.018633     93.909754   3867.314061     19.549984   

                x21           x22           x23           x25           x26  \
count  40000.000000  37613.000000  40000.000000  40000.000000  37567.000000   
mean      11.030799     72.135445      0.202855      4.979892      0.001688   
std       15.652503     26.890151      1.020094      2.442622      1.562125   
min       -3.819778      4.263648     -3.943834     -2.489909     -6.516479   
25%        1.349311     52.710060     -0.484283      3.256295     -1.050565   
50%        5.080475     68.963429      0.198314      4.846035      0.001465   
75%       14.648950     88.047645      0.889074      6.529241      1.061446   
max      196.185637    241.587355      4.713963     18.691319      6.696843   

                x27           x28           x29          x30           x32  \
count  40000.000000  40000.000000  40000.000000  7664.000000  40000.000000   
mean     999.260857     15.022117      1.009982     0.020762      0.552148   
std      104.197073      3.669128      1.418182     1.565846      1.893282   
min      604.067215     -1.074573     -4.165802    -4.775358     -3.966788   
25%      928.783472     12.534429      0.023706    -1.094994     -0.

In [33]:
# show correlation
px.imshow(train.corr(), aspect='auto', title='Train Correlations')

In [34]:
# distribution of object columns
for col in train.select_dtypes('object'): px.histogram(train[col], title='Distribution of '+str(col), template='presentation').show()

The most common days are Wednesday Tuesday and Monday. The distribution of gender is balanced. Column x31 is distributed towards no, while the most common states are California and Texas. The months are distributed towards the winter and summer months. The most popular insurance companies are Progressive and Allstate, while the least common is Geico. The most common car manufacturer is Ford, while the least common is Buick. Column x93 is distributed towards no, while x99 is distributed towards yes. The distribution of these columns are likely to change after imputation. 

### <a id='toc1_2_2_'></a>[Test](#toc0_)

In [35]:
# values of column
test.x3.value_counts(dropna=False)

Wednesday    1224
Friday       1089
Tuesday      1010
Monday       1005
Sunday        953
Saturday      846
Thursday      702
Tue           688
Wed           524
Mon           522
Thur          426
Sat           425
Fri           382
Sun           204
Name: x3, dtype: int64

In [36]:
# being consistent with labeling, short notation
test.x3 = test.x3.str.replace('Sunday', 'Sun')
test.x3 = test.x3.str.replace('Monday', 'Mon')
test.x3 = test.x3.str.replace('Tuesday', 'Tue')
test.x3 = test.x3.str.replace('Wednesday', 'Wed')
test.x3 = test.x3.str.replace('Thursday', 'Thur')
test.x3 = test.x3.str.replace('Friday', 'Fri')
test.x3 = test.x3.str.replace('Saturday', 'Sat')

We combined the corresponding days to the shorthand notation. 

In [37]:
# values of column
test.x24.value_counts(dropna=False)

female    4532
male      4499
NaN        969
Name: x24, dtype: int64

Missing values need to be imputed. 

In [38]:
# check values
test.x33.value_counts(dropna=False)

NaN               1770
California         841
Texas              593
Florida            475
New York           462
Pennsylvania       321
Illinois           306
Ohio               278
Michigan           245
North Carolina     238
Georgia            236
New Jersey         204
Washington         189
Virginia           188
Massachusetts      178
Indiana            162
Colorado           160
Tennessee          157
Oklahoma           153
Missouri           153
Alabama            149
Minnesota          148
Wisconsin          145
Maryland           139
South Carolina     132
Arizona            124
Louisiana          119
Kentucky           114
Arkansas           113
Utah               109
Oregon             102
Connecticut        100
Iowa                89
Nevada              88
Kansas              87
Mississippi         85
Nebraska            77
New Hampshire       73
Idaho               67
West Virginia       65
New Mexico          62
Rhode Island        57
Maine               54
South Dakot

Again, there are 52 values for a missing value with the most counts. 

In [39]:
# Change values to 1
test.x39 = test.x39.str.replace('5-10 miles', '1').astype(int)

All rows of this column are the same, so we will change the value to 1. 

In [40]:
# checking values
test.x60.value_counts(dropna=False)

August       2055
July         2050
December     2028
January      1935
September     295
June          279
February      277
April         240
November      238
May           211
March         210
October       182
Name: x60, dtype: int64

No duplicate naming is seen here, and all 12 months are present. 

In [41]:
# checking values
test.x65.value_counts(dropna=False)

progressive    2703
allstate       2686
esurance       1828
farmers        1451
geico          1332
Name: x65, dtype: int64

This column represents the different insurance companies. 

In [42]:
# checking values
test.x77.value_counts(dropna=False)

ford         2325
NaN          2318
chevrolet    1265
subaru       1209
mercedes     1081
toyota        903
nissan        617
buick         282
Name: x77, dtype: int64

This column represents different vehicle manufacturers.

In [43]:
# checking values
test.x93.value_counts(dropna=False)

no     8848
yes    1152
Name: x93, dtype: int64

In [44]:
# values of column
test.x99.value_counts(dropna=False)

yes    6700
NaN    3300
Name: x99, dtype: int64

Missing values in this column are more likely to be no, rather than missing yes values. Therefore, we will fill in missing vales with no, just as we did with the training set. 

In [45]:
# fill missing values with no
test.x99.fillna('no', inplace=True)

In [46]:
# check proper implementation
test.x99.value_counts(dropna=False)

yes    6700
no     3300
Name: x99, dtype: int64

Filled missing values with no.

In [47]:
train.describe()

y            x1            x2            x4            x5  \
count  40000.000000  40000.000000  40000.000000  40000.000000  37572.000000   
mean       0.145075      2.999958     20.004865      0.002950      0.005396   
std        0.352181      1.994490      1.604291      1.462185      1.297952   
min        0.000000     -3.648431     13.714945     -5.137161     -5.616412   
25%        0.000000      1.592714     18.921388     -1.026798     -0.872354   
50%        0.000000      2.875892     20.005944      0.002263      0.008822   
75%        0.000000      4.270295     21.083465      1.043354      0.892467   
max        1.000000     13.837591     27.086468      5.150153      5.698128   

                 x6            x7            x8            x9           x10  \
count  40000.000000  40000.000000  40000.000000  40000.000000  40000.000000   
mean       0.007234      0.000033      0.004371      2.722334      0.490339   
std        1.358551      0.009965      1.447223      1.966828      1.029863   
min       -6.113153     -0.043800     -6.376810     -3.143438     -3.538129   
25%       -0.909831     -0.006700     -0.971167      1.340450     -0.207833   
50%        0.007335      0.000100      0.002226      2.498876      0.486926   
75%        0.926222      0.006800      0.985023      3.827712      1.182994   
max        5.639372      0.037900      5.869889     18.006669      4.724186   

                x11           x12           x13           x14           x15  \
count  34890.000000  40000.000000  40000.000000  30136.000000  40000.000000   
mean     100.008988      3.039317      3.881807      0.787999      0.011162   
std       13.343010      3.575534      2.678838      0.751117      1.480175   
min       50.526543     -5.846331     -3.060994     -0.338985     -6.141315   
25%       91.056682     -0.200773      1.987650      0.189364     -0.986405   
50%      100.020965      3.073967      3.444608      0.677067      0.016980   
75%      109.025025      6.266835      5.319072      1.267256      1.007430   
max      148.784484     11.149273     25.634165      4.291924      5.930678   

                x16           x17           x18           x19           x20  \
count  28788.000000  40000.000000  40000.000000  40000.000000  40000.000000   
mean     100.702408      8.005758     79.936742     -5.028013      4.962774   
std        1.058560      2.270345      6.514228   1001.312630      3.544050   
min       99.131018     -1.384508     66.756855  -4166.106634     -9.561032   
25%       99.857805      6.465327     74.015148   -682.694719      2.558445   
50%      100.540700      8.003181     79.857023      0.692233      4.982334   
75%      101.371152      9.537869     85.907545    670.404666      7.337529   
max      104.753426     18.018633     93.909754   3867.314061     19.549984   

                x21           x22           x23           x25           x26  \
count  40000.000000  37613.000000  40000.000000  40000.000000  37567.000000   
mean      11.030799     72.135445      0.202855      4.979892      0.001688   
std       15.652503     26.890151      1.020094      2.442622      1.562125   
min       -3.819778      4.263648     -3.943834     -2.489909     -6.516479   
25%        1.349311     52.710060     -0.484283      3.256295     -1.050565   
50%        5.080475     68.963429      0.198314      4.846035      0.001465   
75%       14.648950     88.047645      0.889074      6.529241      1.061446   
max      196.185637    241.587355      4.713963     18.691319      6.696843   

                x27           x28           x29          x30           x32  \
count  40000.000000  40000.000000  40000.000000  7664.000000  40000.000000   
mean     999.260857     15.022117      1.009982     0.020762      0.552148   
std      104.197073      3.669128      1.418182     1.565846      1.893282   
min      604.067215     -1.074573     -4.165802    -4.775358     -3.966788   
25%      928.783472     12.534429      0.023706    -1.094994     -0.

In [48]:
# summary statistics on data
test.describe()

x1            x2            x4           x5            x6  \
count  10000.000000  10000.000000  10000.000000  9398.000000  10000.000000   
mean       2.944648     20.003002      0.004528     0.001215      0.001926   
std        2.018091      1.600368      1.449873     1.290027      1.363301   
min       -2.639067     13.790389     -4.768309    -4.662646     -5.720785   
25%        1.522883     18.926348     -1.025638    -0.878598     -0.931918   
50%        2.817275     20.013331     -0.007336    -0.009562      0.001364   
75%        4.223699     21.083448      1.041062     0.882272      0.925603   
max       11.737364     25.808760      4.653302     4.709272      5.096100   

                 x7            x8            x9           x10          x11  \
count  10000.000000  10000.000000  10000.000000  10000.000000  8671.000000   
mean       0.000008     -0.003416      2.710221      0.506369    99.915979   
std        0.009927      1.442214      1.985433      1.028552    13.254583   
min       -0.036100     -5.627568     -3.160208     -3.452189    51.489501   
25%       -0.006800     -0.978422      1.328622     -0.196678    90.981197   
50%        0.000100      0.000347      2.467988      0.509366    99.918218   
75%        0.006700      0.980095      3.797335      1.200406   108.722557   
max        0.048300      5.326779     17.165790      4.666843   148.312826   

                x12           x13          x14           x15          x16  \
count  10000.000000  10000.000000  7572.000000  10000.000000  7247.000000   
mean       3.019374      3.926723     0.784069      0.012419   100.727360   
std        3.586150      2.706451     0.746441      1.482391     1.060159   
min       -5.039053     -2.918862    -0.338883     -6.013757    99.131027   
25%       -0.203236      1.991729     0.191783     -0.988190    99.885403   
50%        3.083938      3.481996     0.678295      0.014545   100.581635   
75%        6.243080      5.322923     1.260943      1.004756   101.403862   
max       11.102173     22.916481     4.793638      5.780608   104.753426   

                x17           x18           x19           x20           x21  \
count  10000.000000  10000.000000  10000.000000  10000.000000  10000.000000   
mean       8.027597     80.026084     -0.554811      4.987877     11.117466   
std        2.283019      6.547863   1006.365662      3.547695     15.825830   
min       -0.264370     66.471523  -4497.412230     -8.721968     -3.094312   
25%        6.457095     74.074136   -671.622956      2.552523      1.359686   
50%        8.027620     79.973740     10.071374      4.989075      5.151254   
75%        9.551301     86.043355    689.172557      7.413721     14.573628   
max       16.332891     92.750969   3869.733323     19.075814    168.295257   

               x22           x23           x25          x26           x27  \
count  9387.000000  10000.000000  10000.000000  9383.000000  10000.000000   
mean     72.091235      0.189215      5.011489    -0.011677    999.005034   
std      27.229397      1.039170      2.437551     1.569508    104.846352   
min       2.816051     -3.504739     -3.035988    -5.798616    615.307402   
25%      52.540203     -0.514637      3.299264    -1.042946    929.692219   
50%      68.791299      0.186177      4.854312    -0.007550    997.718354   
75%      88.081697      0.902518      6.604764     1.058635   1069.712621   
max     212.245584      3.961364     16.545180     6.185420   1356.405814   

                x28           x29          x30           x32           x34  \
count  10000.000000  10000.000000  1915.000000  10000.000000  10000.000000   
mean      14.992886      0.978150     0.006684      0.550535     53.078686   
std        3.676316      1.401266     1.587620      1.874100      5.845842   
min        1.870244     -3.170093    -4.574698     -4.073306     28.166134   
25%       12.498954      0.001232    -1.144359     -0.475393     49.058566   
50%       15.018232      0.890432     0.002

In [49]:
# distribution of object columns
for col in test.select_dtypes('object'): px.histogram(test[col], title='Distribution of '+ str(col), template='presentation').show()

We se similar distributions in these columns to the respective columns in the training set. 

### <a id='toc1_2_3_'></a>[EDA Conclusions](#toc0_)

We observe some patterns in the dataset. We see certain weekdays and certain months are more prevalent in the datasets. Comparing the train and test datasets, we see many columns have similar distributions. 

## <a id='toc1_3_'></a>[Preprocessing](#toc0_)

In [50]:
# separate features and target
X = train.drop(columns='y')
y = train.y

In [51]:
# values of the target
y.value_counts()

0    34197
1     5803
Name: y, dtype: int64

Target values are very imbalanced, therefore, we wil train models to optimize AUC or F1 scores. The appropriate metric depends on the specific problem and the business needs.

If the business problem involves minimizing false positives and false negatives equally, then optimizing on AUC may be appropriate, as AUC measures the ability of a model to distinguish between positive and negative classes. 

However, if the business problem is such that minimizing false positives is more important than minimizing false negatives, or vice versa, then optimizing on F1 score may be more appropriate. F1 score is the harmonic mean of precision and recall and is a good metric to use when there is an uneven class distribution.

In [52]:
# ordinal encoding days and months in order
weekday_names = ['Mon', 'Tue', 'Wed', 'Thur', 'Fri', 'Sat', 'Sun']
month_names = ['January', 'February', 'March', 'April', 'May', 'June', 'July', 'August', 'September', 'October', 'November', 'December']

encoder_day = OrdinalEncoder(categories=[weekday_names])
encoder_month = OrdinalEncoder(categories=[month_names])

days = pd.DataFrame(encoder_day.fit_transform(X.x3.to_numpy().reshape(-1,1)), columns=['day'])
months = pd.DataFrame(encoder_month.fit_transform(X.x60.to_numpy().reshape(-1,1)), columns=['month'])

In [53]:
# replace columns with ordinal columns 
X['x3'] = days
X['x60'] = months

In [54]:
# check for proper implementation
X.head()

x1         x2   x3        x4        x5        x6      x7        x8  \
0  0.165254  18.060003  2.0  1.077380 -1.339233 -1.584341  0.0062  0.220784   
1  2.441471  18.416307  4.0  1.482586  0.920817 -0.759931  0.0064  1.192441   
2  4.427278  19.188092  3.0  0.145652  0.366093  0.709962 -0.0008  0.952323   
3  3.925235  19.901257  1.0  1.763602 -0.251926 -0.827461 -0.0057 -0.520756   
4  2.868802  22.202473  6.0  3.405119  0.083162  1.381504  0.0109 -0.732739   

         x9       x10         x11       x12       x13       x14       x15  \
0  1.816481  1.171788  109.626841  4.644568  4.814885  1.541740 -0.587361   
1  3.513950  1.419900   84.079367  1.459868  1.443983       NaN -1.165869   
2  0.782974 -1.247022   95.375221  1.098525  1.216059  0.450624  0.211685   
3  1.825586  2.223038   96.420382 -1.390239  3.962961       NaN -2.046856   
4  2.151990 -0.275406   90.769952  7.230125  3.877312  0.392002 -1.201565   

          x16       x17        x18          x19       x20        x21  \
0  101.906052  4.278444  77.709700  -908.650758  7.328029  36.601967   
1  100.112121  8.487132  70.808566 -1864.962288  6.796408   3.789176   
2   99.215210  8.601193  75.922820  -543.187403  3.802395   7.407996   
3         NaN  6.611554  74.966925  -182.626381  7.728963   8.136213   
4  100.626558  9.103015  77.977156   967.007091  2.272765  24.452102   

          x22       x23     x24       x25       x26          x27        x28  \
0  126.384294  1.264713  female  3.834082  2.352406   905.491445  14.779467   
1   93.037021  0.346201    male  4.345028  1.651579   868.784447  25.914680   
2   71.022413  0.070968    male  4.332644 -0.375737  1077.233497  13.177479   
3  121.610846  0.700954    male  7.294990 -0.603983  1051.655489  17.006528   
4   56.492317 -1.102387    male  6.313827  0.429187   949.904947  16.962710   

        x29  x30  x31       x32        x33        x34       x35        x36  \
0  0.752524  NaN   no -0.597288   Colorado  46.667221  3.159002  69.444841   
1  1.445294  NaN   no  1.127376  Tennessee  47.928569 -1.013712  61.289132   
2  4.174536  NaN   no  2.605279      Texas  56.674425  0.108486  69.798923   
3  2.347355  NaN   no  1.071202  Minnesota  59.154933  1.319711  65.408246   
4  0.510985  NaN  yes  2.283921   New York  46.445617  0.022747  66.662910   

         x37        x38  x39        x40            x41       x42       x43  \
0  32.450076        NaN    1  18.129499            NaN  0.904626  1.227266   
1  35.521824  31.526217    1  11.389081   99074.100620 -1.157897 -0.822055   
2  30.684074  31.049447    1  14.372443  100087.339539  0.869508  0.150728   
3  34.401290  48.363690    1  13.191173  100934.096543       NaN -0.965711   
4  31.135261  31.819899    1  17.210430            NaN       NaN  1.012093   

        x44       x45       x46        x47        x48        x49          x50  \
0  0.703326 -0.810371  0.234654  53.359113  58.251700  16.084987  1602.756464   
1 -0.851141  2.651773  1.104631  37.728834  56.052749        NaN  3350.837875   
2       NaN -0.856591 -2.561083  50.236892  63.975108   6.998154  3756.910196   
3       NaN  0.422522 -2.123048  41.857197  59.226119        NaN  1961.609788   
4       NaN -0.348240  3.477451  47.844153  55.921988        NaN  2345.195505   

        x51        x52        x53       x54       x55       x56  x57  \
0  2.740134   7.617666  72.167186  0.166127       NaN -1.532562  NaN   
1  1.995635        NaN  73.964560       NaN       NaN  0.956001  NaN   
2  1.772648  15.057485  59.428690  1.844493       NaN  4.127857  NaN   
3  3.155214        NaN  68.671023 -1.020225  5.833712  0.663759  NaN   
4  3.253079  14.193721  71.853326  0.926779  4.115990 -2.273628  NaN   

          x58  x59  x60       x61       x62       x63        x64       x65  \
0  300.629990    0  7.0  9.840873  6.600008  1.252479  46.992716   farmers   
1  300.629990    0  3.0  6.939395  3.864254  0.057936  48.216622  allstate   
2  182.369349    0  8.0  6.228138  1.370661 -0.239705  54.120933     ge

Encoding all columns with ordinal encoding did not retain the order of days and months. Since there appears to be a trend in the data with respect to days and months, we want to retain the proper order of these labels. So we will encode these columns first, and then encode the other categorical columns later. 

In [55]:
# ordinal encoding dataframe
encoder = OrdinalEncoder()
data_ordinal = pd.DataFrame(encoder.fit_transform(X), columns=X.columns)

In [56]:
# looking at ordinal implementation
data_ordinal.head()

x1       x2   x3       x4       x5       x6     x7       x8       x9  \
0   2636.0   4580.0  2.0  30185.0   5615.0   4774.0  392.0  22341.0  13914.0   
1  16497.0   6471.0  4.0  33250.0  28301.0  11420.0  394.0  31629.0  27889.0   
2  30826.0  12108.0  3.0  21417.0  22803.0  27793.0  322.0  29574.0   5837.0   
3  27774.0  18904.0  1.0  35046.0  15671.0  10767.0  273.0  14362.0  14024.0   
4  19875.0  36426.0  6.0  39550.0  19574.0  33631.0  439.0  12189.0  16942.0   

       x10      x11      x12      x13      x14      x15      x16      x17  \
0  29683.0  26641.0  24603.0  27718.0  25021.0  13624.0  24641.0   2029.0   
1  32479.0   4081.0  15377.0   6674.0      NaN   8515.0   9827.0  23273.0   
2   1798.0  12652.0  14287.0   5481.0  11551.0  21995.0    745.0  24076.0   
3  37901.0  13739.0   5189.0  23110.0      NaN   3350.0      NaN  10804.0   
4   9096.0   8500.0  33821.0  22603.0  10668.0   8249.0  15125.0  27373.0   

       x18      x19      x20      x21      x22      x23  x24      x25  \
0  16490.0   7333.0  29914.0  37300.0  36193.0  33869.0  0.0  13406.0   
1   3069.0   1289.0  27873.0  17523.0  30047.0  22086.0  1.0  16646.0   
2  13450.0  11829.0  14809.0  23411.0  19958.0  17865.0  1.0  16583.0   
3  11750.0  17137.0  31279.0  24310.0  35771.0  27330.0  1.0  33131.0   
4  16964.0  33423.0   9015.0  34557.0  11458.0   3964.0  1.0  28803.0   

       x26      x27      x28      x29  x30  x31      x32   x33      x34  \
0  34953.0   7342.0  18870.0  17961.0  NaN  0.0   8761.0   5.0   5534.0   
1  31953.0   4232.0  39890.0  25499.0  NaN  0.0  30018.0  42.0   7763.0   
2  15157.0  30978.0  12242.0  39015.0  NaN  0.0  36751.0  43.0  29507.0   
3  13058.0  27691.0  28147.0  33073.0  NaN  0.0  29521.0  23.0  34252.0   
4  22744.0  12786.0  27976.0  15206.0  NaN  1.0  36101.0  32.0   5177.0   

       x35      x36      x37      x38  x39      x40      x41      x42  \
0  35507.0  17928.0  26493.0      NaN  0.0  30473.0      NaN  18244.0   
1   1332.0    818.0  36324.0  16254.0  0.0   7910.0   7539.0    246.0   
2   7846.0  19298.0  18419.0  15992.0  0.0  18072.0  16083.0  17975.0   
3  21569.0   5607.0  33636.0  26159.0  0.0  14278.0  23126.0      NaN   
4   7039.0   8662.0  20525.0  16421.0  0.0  27251.0      NaN      NaN   

       x43     x44      x45      x46      x47      x48      x49      x50  \
0  30169.0  2539.0   4043.0  21925.0  30969.0  14989.0  26947.0  12040.0   
1   4003.0   449.0  29980.0  29108.0    122.0   9410.0      NaN  36254.0   
2  14610.0     NaN   3614.0   2849.0  20799.0  30518.0   3242.0  38315.0   
3   3094.0     NaN  16012.0   4497.0   1327.0  17692.0      NaN  17752.0   
4  27379.0     NaN   8346.0  38811.0  12611.0   9102.0      NaN  24220.0   

       x51      x52      x53      x54      x55      x56  x57     x58  x59  \
0  31951.0  15274.0  26782.0  14960.0      NaN   3220.0  NaN  2131.0  0.0   
1  26288.0      NaN  31485.0      NaN      NaN  24836.0  NaN  2131.0  0.0   
2  24182.0  21820.0    648.0  24832.0      NaN  39610.0  NaN   772.0  0.0   
3  34180.0      NaN  15824.0   6110.0  20465.0  21763.0  NaN  2131.0  0.0   
4  34641.0  21353.0  25830.0  20422.0  16392.0   1122.0  NaN   433.0  0.0   

   x60      x61      x62      x63      x64  x65      x66     x67      x68  \
0  7.0  15875.0  35569.0  30199.0   9518.0  2.0  31629.0  1100.0  21509.0   
1  3.0   8047.0  22203.0  19444.0  12540.0  0.0  27534.0  1516.0  37266.0   
2  8.0   5761.0   4654.0  16393.0  27628.0  3.0  19654.0  1516.0  27505.0   
3  8.0   5037.0    733.0  22139.0  28895.0  3.0  15027.0  1516.0  20059.0   
4  0.0  10091.0   4315.0  23128.0  21459.0  3.0  17941.0  1516.0  14109.0   

       x69      x70     x71      x72      x73      x74      x75      x76  x77  \
0  25740.0  12971.0   877.0  28345.0  26179.0      NaN      NaN      NaN  3.0   
1  18320.0  29704.0  1525.0  12557.0  25015.0   3315.0  13826.0   2344.0  3.0   
2  11071.0  29537.0  1525.0  15810.0  29606.0  14935.0  18277.0    840.0  5.0   
3  33606.0  19389.0   516.0 

In [57]:
# imputing missing values
imputer = SimpleImputer()
imp_ord = imputer.fit_transform(data_ordinal)

In [58]:
# checking the shape of the imputed dataframe
imp_ord.shape

(40000, 100)

In [59]:
# scaling the imputed dataframe
scaler = StandardScaler()
X_final = scaler.fit_transform(imp_ord)

In [60]:
# shape of the final dataframe
X_final.shape

(40000, 100)

In [61]:
# train and valid split
X_train, X_valid, y_train, y_valid = train_test_split(
    X_final, y, test_size=0.25, random_state=19)

#### <a id='toc1_3_1_1_'></a>[Preprocessing Conclusions](#toc0_)

We preprocessed the data to convert the categorical columns into numerically labeled columns. Although some of our models selected can handle categorical values, we prefer to train the models on continuous values. Finally, we split the data into train and validation sets for hyperparameter tuning. 

## <a id='toc1_4_'></a>[Modeling](#toc0_)

### <a id='toc1_4_1_'></a>[Tuning with Grid Search CV](#toc0_)

In [62]:
# Gridsearch CV for hyperparameter tuning
import lightgbm as lgb

# Create a LightGBM dataset
lgb_train = lgb.Dataset(X_train, y_train)
lgb_valid = lgb.Dataset(X_valid, y_valid, reference=lgb_train)

# Define the parameter grid for the LightGBM model
param_grid = {
    'boosting_type': ['gbdt'],
    'num_leaves': [5, 10, 15],
    'max_depth': [3, 4, 5],
    'learning_rate': [0.1],
    'n_estimators': [75, 100, 200, 300],
    'random_state': [19]
}

# Define the parameters for the LightGBM model
params = {
    'objective': 'binary',
    'metric': 'auc',
}

# Create the GridSearchCV object
grid_search = GridSearchCV(LGBMClassifier(**params), param_grid, cv=2, scoring='roc_auc',verbose=3, n_jobs=-1)

# Fit the GridSearchCV object to the data
grid_search.fit(X_train, y_train)

# Print the best parameters and the best score
print("Best parameters: ", grid_search.best_params_)
print("Best score: ", grid_search.best_score_)


Fitting 2 folds for each of 36 candidates, totalling 72 fits
Best parameters:  {'boosting_type': 'gbdt', 'learning_rate': 0.1, 'max_depth': 3, 'n_estimators': 200, 'num_leaves': 5, 'random_state': 19}
Best score:  0.7938918654981924


We used Grid Search CV to tune hyperparameters of each model we selected, and we will use the best parameters in the pipeline. 

### <a id='toc1_4_2_'></a>[Tuning Neural Network](#toc0_)

In [63]:
# tuning neural network
optimizer = Adam(learning_rate=0.001)

model = keras.models.Sequential()
model.add(
    keras.layers.Dense(
        units=10, input_dim=X_train.shape[1], activation='relu'
    )
)
model.add(keras.layers.Dense(
        units=5, activation='relu'
    ))
model.add(keras.layers.Dense(
        units=1, activation='sigmoid'
    ))
model.compile(loss='binary_crossentropy', optimizer=optimizer, metrics=['AUC'])
model.fit(X_train, y_train, epochs=10, verbose=2,
          validation_data=(X_valid, y_valid))

Epoch 1/10
938/938 - 3s - loss: 0.4124 - auc: 0.6421 - val_loss: 0.3676 - val_auc: 0.7158 - 3s/epoch - 3ms/step
Epoch 2/10
938/938 - 2s - loss: 0.3691 - auc: 0.7442 - val_loss: 0.3565 - val_auc: 0.7438 - 2s/epoch - 2ms/step
Epoch 3/10
938/938 - 2s - loss: 0.3588 - auc: 0.7654 - val_loss: 0.3508 - val_auc: 0.7570 - 2s/epoch - 2ms/step
Epoch 4/10
938/938 - 1s - loss: 0.3524 - auc: 0.7774 - val_loss: 0.3482 - val_auc: 0.7624 - 1s/epoch - 2ms/step
Epoch 5/10
938/938 - 2s - loss: 0.3472 - auc: 0.7864 - val_loss: 0.3447 - val_auc: 0.7687 - 2s/epoch - 2ms/step
Epoch 6/10
938/938 - 2s - loss: 0.3432 - auc: 0.7930 - val_loss: 0.3454 - val_auc: 0.7678 - 2s/epoch - 2ms/step
Epoch 7/10
938/938 - 2s - loss: 0.3406 - auc: 0.7971 - val_loss: 0.3430 - val_auc: 0.7720 - 2s/epoch - 2ms/step
Epoch 8/10
938/938 - 1s - loss: 0.3386 - auc: 0.8003 - val_loss: 0.3436 - val_auc: 0.7715 - 1s/epoch - 2ms/step
Epoch 9/10
938/938 - 2s - loss: 0.3369 - auc: 0.8026 - val_loss: 0.3443 - val_auc: 0.7715 - 2s/epoch - 2

A more complicated neural network with more layers and epochs can lead to overfitting. We trained models with 0.99 AUC with the training set, but with much lower scores with the validation set. This provides evidence of overfitting, or other factors could be contributing to lower validation scores. 

#### <a id='toc1_4_2_1_'></a>[Model Pipeline](#toc0_)

In [65]:
# Classifier pipeline
pipe_lr = Pipeline([('imputer', SimpleImputer()), ('scalar1', StandardScaler()), ('lr_classifier', LogisticRegression(random_state=19, max_iter=2000))])
pipe_dt = Pipeline([('imputer', SimpleImputer()), ('scalar1', StandardScaler()), ('dt_classifier', DecisionTreeClassifier(random_state=19, max_depth=3))])
pipe_rf = Pipeline([('imputer', SimpleImputer()), ('scalar1', StandardScaler()), ('rf_classifier', RandomForestClassifier(random_state=19, n_estimators=40))])
pipe_sv = Pipeline([('imputer', SimpleImputer()), ('scalar1', StandardScaler()), ('svm_classifier', svm.LinearSVC(random_state=19, max_iter=2000))])
pipe_xg = Pipeline([('imputer', SimpleImputer()), ('scalar1', StandardScaler()), ('xg_classifier', XGBClassifier(random_state=19, n_estimators=100, learning_rate=0.1, eval_metric='auc', max_depth=4))])
pipe_lb = Pipeline([('imputer', SimpleImputer()), ('scalar1', StandardScaler()), ('lb_classifier', LGBMClassifier(boosting_type='gbdt', random_state=19, objective='binary', metric='auc', n_estimators=100, learning_rate=0.1))])
pipe_ml = Pipeline([('imputer', SimpleImputer()), ('scalar1', StandardScaler()), ('ml_classifier', MLPClassifier(max_iter=200, random_state=19, early_stopping=True, n_iter_no_change=10))])

pipelines = [pipe_lr, pipe_dt, pipe_rf, pipe_sv, pipe_xg, pipe_lb, pipe_ml]

best_auc = 0
best_classifier = 0
best_pipeline = ""

pipe_dict = {0: 'Logistic Regression', 1: 'Decision Tree', 2: 'Random Forest', 3: 'SVM', 4: 'XG Boost', 5: 'Light GBM', 6:'Neural Network'}

# Use cross-validation to evaluate the models
for i, model in enumerate(pipelines):
    model.fit(X_train, y_train)
    scores = cross_val_score(model, data_ordinal, y, cv=5, scoring='roc_auc')
    print('{} Cross-Validation Accuracy: {:.2f}'.format(pipe_dict[i], scores.mean()))
    if scores.mean() > best_auc:
        best_auc = scores.mean()
        best_pipeline = model
        best_classifier = i

# Print the best classifier
print('\nClassifier with the best AUC-ROC score: {}'.format(pipe_dict[best_classifier]))

Logistic Regression Cross-Validation Accuracy: 0.75
Decision Tree Cross-Validation Accuracy: 0.70
Random Forest Cross-Validation Accuracy: 0.72


c:\Users\XIX\anaconda3\lib\site-packages\sklearn\svm\_base.py:1206: ConvergenceWarning:

Liblinear failed to converge, increase the number of iterations.

c:\Users\XIX\anaconda3\lib\site-packages\sklearn\svm\_base.py:1206: ConvergenceWarning:

Liblinear failed to converge, increase the number of iterations.

c:\Users\XIX\anaconda3\lib\site-packages\sklearn\svm\_base.py:1206: ConvergenceWarning:

Liblinear failed to converge, increase the number of iterations.

c:\Users\XIX\anaconda3\lib\site-packages\sklearn\svm\_base.py:1206: ConvergenceWarning:

Liblinear failed to converge, increase the number of iterations.

c:\Users\XIX\anaconda3\lib\site-packages\sklearn\svm\_base.py:1206: ConvergenceWarning:

Liblinear failed to converge, increase the number of iterations.

c:\Users\XIX\anaconda3\lib\site-packages\sklearn\svm\_base.py:1206: ConvergenceWarning:

Liblinear failed to converge, increase the number of iterations.



SVM Cross-Validation Accuracy: 0.75
XG Boost Cross-Validation Accuracy: 0.79
Light GBM Cross-Validation Accuracy: 0.79
Neural Network Cross-Validation Accuracy: 0.75

Classifier with the best AUC-ROC score: XG Boost


We tried to implement two other imputers, KNN and iterative imputer. However, they were too computationally intensive for this system. KNN and iterative imputer use machine learning to impute the missing values, and increased accuracy of the imputed values comes at a cost in terms of model training time. Consequently, we will use simple imputation. The models were trained on the training set, and cross validation was used to determine average AUC scores. 

In [66]:
# dummy model
pipe_dm = Pipeline([('imputer', SimpleImputer()), ('scalar1', StandardScaler()), ('dm_classifier', DummyClassifier(random_state=19, strategy='most_frequent'))])
pipe_dm.fit(X_train, y_train)

scores = cross_val_score(pipe_dm, data_ordinal, y, cv=5, scoring='roc_auc') 
final_score = sum(scores) / len(scores)
print('Average model AUC ROC score:', final_score)

Average model AUC ROC score: 0.5


In [67]:
# accuracy functionof dummy model
from sklearn.metrics import accuracy_score
accuracy_score(y_valid, pipe_dm.predict(X_valid))

0.861

A dummy model was trained to illustrate two things: the effect of class imbalance, and the difference between AUC and accuracy. This dummy is a baseline model that disregards the features, and always predicts the majority class, 0. As we can see, the accuracy of the model is high, while the AUC score is 0.5. However, accuracy is not a useful metric with imbalanced targets, because it does not properly illustrate the model's performance on the minority class with false negatives. 

### <a id='toc1_4_3_'></a>[Compare Model Scores](#toc0_)

In [68]:
# series of model scores
data = {'Logistic Regression': 0.7496, 'Decision Tree': 0.6955 , 'Random Forest': 0.7243, 'SVM': 0.7493, 'XG Boost': 0.7927, 'Light GBM': 0.7879, 'Neural Network': 0.75}
comp = pd.Series(data, name='AUC Score')

# model scores
px.scatter(comp, color=comp.index, size=comp, title='Model Score Comparison', symbol=comp, labels={'index': 'Model', 'value': 'AUC Score'})

#### <a id='toc1_4_3_1_'></a>[Dummy Model AUC](#toc0_)

In [69]:
# dummy model
probabilities_valid = pipe_dm.predict_proba(X_valid)
probabilities_one_valid = probabilities_valid[:, 1]

auc_roc = roc_auc_score(y_valid, probabilities_one_valid)

print(auc_roc)

# ROC AUC curve of results
fpr, tpr, thresholds = roc_curve(y_valid, probabilities_one_valid)

fig = px.area(
    x=fpr, y=tpr,
    title=f'ROC Curve (AUC={auc(fpr, tpr):.4f})',
    labels=dict(x='False Positive Rate', y='True Positive Rate'),
    width=700, height=500
)
fig.add_shape(
    type='line', line=dict(dash='dash'),
    x0=0, x1=1, y0=0, y1=1
)

fig.update_yaxes(scaleanchor="x", scaleratio=1)
fig.update_xaxes(constrain='domain')
fig.show()

0.5


#### <a id='toc1_4_3_2_'></a>[Logistic Regression AUC](#toc0_)

In [70]:
probabilities_valid = pipe_lr.predict_proba(X_valid)
probabilities_one_valid = probabilities_valid[:, 1]

auc_roc = roc_auc_score(y_valid, probabilities_one_valid)

print(auc_roc)

# ROC AUC curve of results
fpr, tpr, thresholds = roc_curve(y_valid, probabilities_one_valid)

fig = px.area(
    x=fpr, y=tpr,
    title=f'ROC Curve (AUC={auc(fpr, tpr):.4f})',
    labels=dict(x='False Positive Rate', y='True Positive Rate'),
    width=700, height=500
)
fig.add_shape(
    type='line', line=dict(dash='dash'),
    x0=0, x1=1, y0=0, y1=1
)

fig.update_yaxes(scaleanchor="x", scaleratio=1)
fig.update_xaxes(constrain='domain')
fig.show()

0.7496001804827915


#### <a id='toc1_4_3_3_'></a>[Decision Tree AUC](#toc0_)

In [71]:
probabilities_valid = pipe_dt.predict_proba(X_valid)
probabilities_one_valid = probabilities_valid[:, 1]

auc_roc = roc_auc_score(y_valid, probabilities_one_valid)

print(auc_roc)

# ROC AUC curve of results
fpr, tpr, thresholds = roc_curve(y_valid, probabilities_one_valid)

fig = px.area(
    x=fpr, y=tpr,
    title=f'ROC Curve (AUC={auc(fpr, tpr):.4f})',
    labels=dict(x='False Positive Rate', y='True Positive Rate'),
    width=700, height=500
)
fig.add_shape(
    type='line', line=dict(dash='dash'),
    x0=0, x1=1, y0=0, y1=1
)

fig.update_yaxes(scaleanchor="x", scaleratio=1)
fig.update_xaxes(constrain='domain')
fig.show()

0.695472388639611


#### <a id='toc1_4_3_4_'></a>[Random Forest AUC](#toc0_)

In [72]:
probabilities_valid = pipe_rf.predict_proba(X_valid)
probabilities_one_valid = probabilities_valid[:, 1]

auc_roc = roc_auc_score(y_valid, probabilities_one_valid)

print(auc_roc)

# ROC AUC curve of results
fpr, tpr, thresholds = roc_curve(y_valid, probabilities_one_valid)

fig = px.area(
    x=fpr, y=tpr,
    title=f'ROC Curve (AUC={auc(fpr, tpr):.4f})',
    labels=dict(x='False Positive Rate', y='True Positive Rate'),
    width=700, height=500
)
fig.add_shape(
    type='line', line=dict(dash='dash'),
    x0=0, x1=1, y0=0, y1=1
)

fig.update_yaxes(scaleanchor="x", scaleratio=1)
fig.update_xaxes(constrain='domain')
fig.show()

0.7242772332656523


#### <a id='toc1_4_3_5_'></a>[SVM AUC](#toc0_)

In [73]:
probabilities_valid = pipe_sv.decision_function(X_valid)
auc_roc = roc_auc_score(y_valid, probabilities_valid)

print(auc_roc)

# ROC AUC curve of results
fpr, tpr, thresholds = roc_curve(y_valid, probabilities_valid)

fig = px.area(
    x=fpr, y=tpr,
    title=f'ROC Curve (AUC={auc(fpr, tpr):.4f})',
    labels=dict(x='False Positive Rate', y='True Positive Rate'),
    width=700, height=500
)
fig.add_shape(
    type='line', line=dict(dash='dash'),
    x0=0, x1=1, y0=0, y1=1
)

fig.update_yaxes(scaleanchor="x", scaleratio=1)
fig.update_xaxes(constrain='domain')
fig.show()

0.749313079153402


#### <a id='toc1_4_3_6_'></a>[XG Boost AUC](#toc0_)

In [74]:
probabilities_valid = pipe_xg.predict_proba(X_valid)
probabilities_one_valid = probabilities_valid[:, 1]

auc_roc = roc_auc_score(y_valid, probabilities_one_valid)

print(auc_roc)

# ROC AUC curve of results
fpr, tpr, thresholds = roc_curve(y_valid, probabilities_one_valid)

fig = px.area(
    x=fpr, y=tpr,
    title=f'ROC Curve (AUC={auc(fpr, tpr):.4f})',
    labels=dict(x='False Positive Rate', y='True Positive Rate'),
    width=700, height=500
)
fig.add_shape(
    type='line', line=dict(dash='dash'),
    x0=0, x1=1, y0=0, y1=1
)

fig.update_yaxes(scaleanchor="x", scaleratio=1)
fig.update_xaxes(constrain='domain')
fig.show()

0.792677955196818


#### <a id='toc1_4_3_7_'></a>[Light GBM AUC](#toc0_)

In [75]:
probabilities_valid = pipe_lb.predict_proba(X_valid)
probabilities_one_valid = probabilities_valid[:, 1]

auc_roc = roc_auc_score(y_valid, probabilities_one_valid)

print(auc_roc)

# ROC AUC curve of results
fpr, tpr, thresholds = roc_curve(y_valid, probabilities_one_valid)

fig = px.area(
    x=fpr, y=tpr,
    title=f'ROC Curve (AUC={auc(fpr, tpr):.4f})',
    labels=dict(x='False Positive Rate', y='True Positive Rate'),
    width=700, height=500
)
fig.add_shape(
    type='line', line=dict(dash='dash'),
    x0=0, x1=1, y0=0, y1=1
)

fig.update_yaxes(scaleanchor="x", scaleratio=1)
fig.update_xaxes(constrain='domain')
fig.show()

0.7878999657416923


##### <a id='toc1_4_3_7_1_'></a>[Modelling Conclusions](#toc0_)

AUC ROC is a metric that compares the True positive rate with the False Positive Rate. The dashed line through the curve represents 0.50, the score of a random model. AUC scores closer to 0 are poor performing, while a perfect AUC score is 1. We see most models perform moderately, when compared to a random model. 


Logistic regression is a model that is simple, fast, and easily interpretable. Logistic regression works well with linearly separable data, and it can handle large datasets with low computational cost. A weakness of this model include its assumption that the input features are linearly separable, which may lead to poor performance, high bias, and underfitting when the data is too complex. 

Decision trees are also easily interpretable, and they can handle categorical data. It can handle categorical data by implementing one-hot encoding. Decision trees can also capture non-linear relationships. Weaknesses includes its inclination to overfit the training data, and not generalize new data. 

Random forest can also handle categorical and continuous data, and it reduces overfitting by using multiple trees. Random forest is less interpretable than the previous methods, and requires hyperparameter tuning to reduce overfitting. 

Linear SVC is good for binary classification tasks, and can handle high-dimensional data. SVC models do not work well with imbalanced classes, can be sensitive to outliers, and are slow to train on large datasets. 

XG boost models can handle both categorical and continuous data, and reduce overfitting by using multiple trees. XG boost models may require significant tuning. 

Light GBM is similar to XG boost, but can handle larger datasets faster and with less memory. Also, this model requires hyperparameter tuning to reduce overfitting. 

MLP models and other neural networks can handle complex relationships between features and targets. Neural networks can be computationally extensive, require hyperparameter tuning, nad can suffer from overfitting. 

Overall, the best model to use depends on the problem at hand, the size and complexity of the data, and the level of interpretability. 




### <a id='toc1_4_4_'></a>[Feature Importance](#toc0_)

#### <a id='toc1_4_4_1_'></a>[Logistic Regression](#toc0_)

In [76]:
# Logistic regression pipeline feature importance
pipe_lr.fit(X_train, y_train)

logreg_classifier = pipe_lr.named_steps['lr_classifier']
logreg_importances = logreg_classifier.coef_
logreg_indices = np.argsort(logreg_importances)[::-1]


In [77]:
# making dataframe of important coefficients
lr_importance = pd.DataFrame(logreg_importances, columns=X.columns)
lr_importance = lr_importance.T
lr_top_10_df = lr_importance.nlargest(10, columns=0)

In [78]:
px.pie(lr_top_10_df, names=lr_top_10_df.index, values=0, title='Top 10 Linear Regression Coefficients')

#### <a id='toc1_4_4_2_'></a>[Decision Tree](#toc0_)

In [79]:
# decision tree pipeline feature importance
pipe_dt.fit(X_train, y_train)

dt_classifier = pipe_dt.named_steps['dt_classifier']
dt_importances = dt_classifier.feature_importances_
dt_indices = np.argsort(dt_importances)[::-1]

top_10_features = []
for f in range(10):
    feature_index = dt_indices[f]
    feature_name = train.columns[feature_index]
    top_10_features.append((feature_name, dt_importances[feature_index]))

dt_top_10_df = pd.DataFrame(top_10_features, columns=['Feature', 'Importance'])


In [80]:
px.pie(dt_top_10_df.head(2), title='Top Features of Decision Tree', names='Feature', values='Importance')

#### <a id='toc1_4_4_3_'></a>[Random Forest](#toc0_)

In [81]:
# random forest pipeline feature importance
pipe_rf.fit(X_train, y_train)

rf_classifier = pipe_rf.named_steps['rf_classifier']
rf_importances = rf_classifier.feature_importances_
rf_indices = np.argsort(rf_importances)[::-1]

top_10_features = []
for f in range(10):
    feature_index = rf_indices[f]
    feature_name = train.columns[feature_index]
    top_10_features.append((feature_name, rf_importances[feature_index]))

rf_top_10_df = pd.DataFrame(top_10_features, columns=['Feature', 'Importance'])


In [82]:
px.pie(rf_top_10_df, title='Top 10 Features of Random Forest', names='Feature', values='Importance')

#### <a id='toc1_4_4_4_'></a>[Support Vector](#toc0_)

In [83]:
# Support vector pipeline feature importance
pipe_sv.fit(X_train, y_train)

svm_classifier = pipe_sv.named_steps['svm_classifier']
svm_importances = svm_classifier.coef_
svm_indices = np.argsort(svm_importances)[::-1]

# making dataframe of important coefficients
sv_importance = pd.DataFrame(svm_importances, columns=X.columns)
sv_importance = sv_importance.T
sv_top_10_df = sv_importance.nlargest(10, columns=0)

c:\Users\XIX\anaconda3\lib\site-packages\sklearn\svm\_base.py:1206: ConvergenceWarning:

Liblinear failed to converge, increase the number of iterations.



In [84]:
px.pie(sv_top_10_df, names=sv_top_10_df.index, values=0, title='Top 10 Support Vector Coefficients')

#### <a id='toc1_4_4_5_'></a>[XG Boost](#toc0_)

In [85]:
# xg boost pipeline feature importance
pipe_xg.fit(X_train, y_train)

xg_classifier = pipe_xg.named_steps['xg_classifier']
xg_importances = xg_classifier.feature_importances_
xg_indices = np.argsort(xg_importances)[::-1]

top_10_features = []
for f in range(10):
    feature_index = xg_indices[f]
    feature_name = train.columns[feature_index]
    top_10_features.append((feature_name, xg_importances[feature_index]))

xg_top_10_df = pd.DataFrame(top_10_features, columns=['Feature', 'Importance'])

In [86]:
px.pie(xg_top_10_df, title='Top 10 Features of XG Boost', names='Feature', values='Importance')

#### <a id='toc1_4_4_6_'></a>[Light GBM](#toc0_)

In [87]:
# light boost pipeline feature importance
pipe_lb.fit(X_train, y_train)

lb_classifier = pipe_lb.named_steps['lb_classifier']
lb_importances = lb_classifier.feature_importances_
lb_indices = np.argsort(lb_importances)[::-1]

top_10_features = []
for f in range(10):
    feature_index = lb_indices[f]
    feature_name = train.columns[feature_index]
    top_10_features.append((feature_name, lb_importances[feature_index]))

lb_top_10_df = pd.DataFrame(top_10_features, columns=['Feature', 'Importance'])

In [88]:
px.pie(lb_top_10_df, title='Top 10 Features of XG Boost', names='Feature', values='Importance')

If scoring metrics can not be used to chose a model, feature importance can help pick a model based on explainability. Explainability is how to take a machine learning model and express the behavior in human terms. With complex models, you can not fully understand how the model parameters impact predictions. With feature importance, we can pick a model based on how it makes predictions, and which features are most important to each model. Even without feature importance, a model can still be selected based on its interpretability, as simpler models are easier to explain to stakeholders. 

Furthermore, we can use visualizations to show how predictions of two models differ from actual values.  A confusion matrix can show true positive and true negative values, and a visualization of the confusion matrix can illustrate the results of the classification model's predictions. 

## <a id='toc1_5_'></a>[Simulate Scoring with Test Set](#toc0_)

In [89]:
# confusion matrix map
fig = go.Figure(data=go.Heatmap(z=[[1205, 185], [8557, 53]], text=[['False Negatives', 'True Positives'], ['True Negatives', 'False Positives']], 
                texttemplate="%{text}", textfont={"size":20}))

fig.show()

In [90]:
# validation predcitions of xg boost
valid_pred_lr = pipe_lr.predict(X_valid)

In [91]:
# confusion matrix of validation set of logistic regression
px.imshow(confusion_matrix(y_valid, valid_pred_lr), text_auto=True, labels=dict(y="Actual", x="Predicted"),
                x=['Negative', 'Positive'],
                y=['Negative', 'Positive'], title='Confusion Matrix of Linear Regression')

The true negative value is 8521, while the true positive value is 112. Overall, the model performed great at predicting the negative class, and poor with the positive class. 

In [92]:
# validation predcitions of xg boost
valid_pred_xg = pipe_xg.predict(X_valid)

In [93]:
# confusion matrix of validation set of xg boost
px.imshow(confusion_matrix(y_valid, valid_pred_xg), text_auto=True, labels=dict(y="Actual", x="Predicted"),
                x=['Negative', 'Positive'],
                y=['Negative', 'Positive'], title='Confusion Matrix of XG boost')

The classification report illustrates the true negative value of 8518 and a true positive vale of 152, which are predicted values that match actual values. Overall, the model was good at predicting the negative class, and poor at predicting the positive class. This is further supported by the false negative value of 1238, which are the instances where the model incorrectly predicted a negative class. We see these trends because the target values are extremely imbalanced, with more negative classes present in the data. 

The confusion matrix on the validation set is used to illustrate how the model will perform on the test set. 

In [94]:
# validation f1 score
f1_score(y_valid, valid_pred_lr)

0.1458852867830424

In [95]:
# classification report 
print(classification_report(y_valid, valid_pred_lr))

              precision    recall  f1-score   support

           0       0.87      0.99      0.93      8610
           1       0.55      0.08      0.15      1390

    accuracy                           0.86     10000
   macro avg       0.71      0.54      0.54     10000
weighted avg       0.82      0.86      0.82     10000



The classification report breaks down the precision and recall of the model with respect to each class. Precision tells us how well the model identifies relevant instances, while recall tells us how well te model captures all relevant instances. A model high precision and recall is a strong model. With the Logistic regression model, we see high precision and recall with the negative class. The positive class has average precision, and very poor recall. Consequently, the f1 score of the negative class is high, while the positive class has a poor f1 score.

In [96]:
# validation f1 score
f1_score(y_valid, valid_pred_xg)

0.18604651162790697

In [97]:
# classification report 
print(classification_report(y_valid, valid_pred_xg))

              precision    recall  f1-score   support

           0       0.87      0.99      0.93      8610
           1       0.62      0.11      0.19      1390

    accuracy                           0.87     10000
   macro avg       0.75      0.55      0.56     10000
weighted avg       0.84      0.87      0.82     10000



In our case with xg boost, we see high precision and recall in the negative class. The positive class has good precision, but poor recall. As F1 score is the harmonic mean of precision and recall, the negative class has a high F1 score, while the positive class has a poor F1 score. 

#### <a id='toc1_5_1_1_'></a>[Test Set scoring Predictions](#toc0_)

Based on the confusion matrices and classification reports, we expect the xg boost model to perform better. The xg boost model had more true positive and true negative values than the logistic regression model, when comparing performance on the validation set. 

## <a id='toc1_6_'></a>[Final Model Predictions](#toc0_)

In [98]:
# final Linear regression
final_lr = pipe_lr.fit(X_final, y)

In [99]:
# Final xg boost model
final_xg = pipe_xg.fit(X_final, y)

Now that we have selected our final models, we use the full training set to fit the models.

In [100]:
# ordinal encoding days and months in order

days_test = pd.DataFrame(encoder_day.fit_transform(test.x3.to_numpy().reshape(-1,1)), columns=['day'])
months_test = pd.DataFrame(encoder_month.fit_transform(test.x60.to_numpy().reshape(-1,1)), columns=['month'])

In [101]:
# replace columns with ordinal columns 
test['x3'] = days_test
test['x60'] = months_test

In [102]:
# preprocessing steps
preprocessor = Pipeline([('ordinal_encoder', OrdinalEncoder()), ('imputer', SimpleImputer()), ('scaler', StandardScaler())])

# Preprocess the test data 
X_test_transformed = preprocessor.fit_transform(test)

In [103]:
# shape of test set
X_test_transformed.shape

(10000, 100)

We follow the same preprocessing steps as the training set, to transform the test set for the model. 

In [104]:
# test set predictions
valid_pred_lr = final_lr.predict_proba(X_test_transformed)
valid_pred_xg = final_xg.predict_proba(X_test_transformed)

In [105]:
# probabilities of positive class
lr_list = valid_pred_lr[:,1].tolist()

In [106]:
# Create a DataFrame from the list
lr_df = pd.DataFrame(lr_list)

# Save the DataFrame to a CSV file
# lr_df.to_csv('predictions/glmresults.csv', index=False, header=False)

In [107]:
# probabilities of positive class
xg_list = valid_pred_xg[:,1].tolist()

In [108]:
# Create a DataFrame from the list
xg_df = pd.DataFrame(xg_list)

# Save the DataFrame to a CSV file
# xg_df.to_csv('predictions/nonglmresults.csv', index=False, header=False)

In [109]:
# logistic regression class predictions
lr_class = pd.DataFrame(final_lr.predict(X_test_transformed))

In [110]:
# class prediction counts
lr_class.value_counts()

0    9792
1     208
dtype: int64

The logistic regression model made 9792 negative predictions, and 208 positive predictions. 

In [111]:
# xg boost class predictions
xg_class = pd.DataFrame(final_xg.predict(X_test_transformed))

In [112]:
# class prediction counts
xg_class.value_counts()

0    9741
1     259
dtype: int64

The xg boost model made 51 more positive predictions than the logistic regression model. 

## <a id='toc1_7_'></a>[Executive Summary](#toc0_)

The linear model is simple and easy to to interpret, however, it assumes a linear relationship between the features and the target. XG boost is a more powerful model that can handle non-linear data, categorical values, and datasets with many features. However, XG boost requires hyperparameter tuning to prevent overfitting, and is often more complex to implement. When it comes to picking between the two models, our main determinant is model performance. If our decision was not based on performance, but on interpretability, we would chose linear regression and show the top coefficients. Based on model performance on the validation set, I expect XG boost to perform better on the test set. In addition, the models in the pipeline that did not assume linearity performed better.  

As the AUC of a model is more often lower on the test set than on the validation set, we assume the XG boost model will perform slightly better on the test set, as it has a slightly higher AUC on the validation set. In addition, the XG boost made more correct predictions in the positive and negative classes, as evident by the confusion matrix of the validation set. We estimate the AUC score of the logistic regression model to be between 0.65-0.8, while the AUC of the xg boost model may be between 0.7-0.85. 

If we cannot use a scoring metric to compare the two models, we can compare the predictions of the two models on the test set. We can compare the true positive and true negative values of both models, as the model with more correct predictions will perform better. We can also compare the false positive and false negative values of both models. 